# NLP example with Transformers from HuggingFace

Example is based on a collection of different online sources, but the most usefull one: https://huggingface.co/docs/transformers/tasks/sequence_classification



To kick things of, we first need to install the necessary libraries...

In [1]:
!pip install transformers datasets sentencepiece evaluate bertviz

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 521.2/521.2 kB 3.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 23.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 84.1/84.1 kB 12.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 157.6/157.6 kB 3.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 115.3/115.3 kB 15.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 17.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 139.3/139.3 kB 18.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 11.8/11.8 MB 33.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 82.0/82.0 kB 12.8 MB/s eta 0:00:00


In [2]:
!pip install transformers[torch]

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 265.7/265.7 kB 2.2 MB/s eta 0:00:00


In [3]:
#pip install ipywidgets
from google.colab import files
uploaded = files.upload()


Saving train.csv to train.csv


In [4]:
!pip install pandas

In [5]:
import pandas  as pd

In [6]:
data = pd.read_csv("train.csv")
data.head(10)

id                                       comment_text  toxic  \
0  0000997932d777bf  Explanation\nWhy the edits made under my usern...      0   
1  000103f0d9cfb60f  D'aww! He matches this background colour I'm s...      0   
2  000113f07ec002fd  Hey man, I'm really not trying to edit war. It...      0   
3  0001b41b1c6bb37e  "\nMore\nI can't make any real suggestions on ...      0   
4  0001d958c54c6e35  You, sir, are my hero. Any chance you remember...      0   
5  00025465d4725e87  "\n\nCongratulations from me as well, use the ...      0   
6  0002bcb3da6cb337       COCKSUCKER BEFORE YOU PISS AROUND ON MY WORK      1   
7  00031b1e95af7921  Your vandalism to the Matt Shirvington article...      0   
8  00037261f536c51d  Sorry if the word 'nonsense' was offensive to ...      0   
9  00040093b2687caa  alignment on this subject and which are contra...      0   

   severe_toxic  obscene  threat  insult  identity_hate  
0             0        0       0       0              0  
1             0        0       0       0              0  
2             0        0       0       0              0  
3             0        0       0       0              0  
4             0        0       0       0              0  
5             0        0       0       0              0  
6             1        1       0       1              0  
7             0        0       0       0              0  
8             0        0       0       0              0  
9             0        0       0       0              0

In [7]:
data.groupby("toxic").describe()

severe_toxic                                                obscene  \
             count      mean       std  min  25%  50%  75%  max     count   
toxic                                                                       
0         144277.0  0.000000  0.000000  0.0  0.0  0.0  0.0  0.0  144277.0   
1          15294.0  0.104289  0.305645  0.0  0.0  0.0  0.0  1.0   15294.0   

                 ... insult      identity_hate                                \
           mean  ...    75%  max         count      mean       std  min  25%   
toxic            ...                                                           
0      0.003625  ...    0.0  1.0      144277.0  0.000714  0.026710  0.0  0.0   
1      0.518242  ...    1.0  1.0       15294.0  0.085131  0.279086  0.0  0.0   

                      
       50%  75%  max  
toxic                 
0      0.0  0.0  1.0  
1      0.0  0.0  1.0  

[2 rows x 40 columns]

In [8]:
toxic_data = data.drop(columns=['severe_toxic','obscene','threat','insult','identity_hate'])
toxic_data

id                                       comment_text  \
0       0000997932d777bf  Explanation\nWhy the edits made under my usern...   
1       000103f0d9cfb60f  D'aww! He matches this background colour I'm s...   
2       000113f07ec002fd  Hey man, I'm really not trying to edit war. It...   
3       0001b41b1c6bb37e  "\nMore\nI can't make any real suggestions on ...   
4       0001d958c54c6e35  You, sir, are my hero. Any chance you remember...   
...                  ...                                                ...   
159566  ffe987279560d7ff  ":::::And for the second time of asking, when ...   
159567  ffea4adeee384e90  You should be ashamed of yourself \n\nThat is ...   
159568  ffee36eab5c267c9  Spitzer \n\nUmm, theres no actual article for ...   
159569  fff125370e4aaaf3  And it looks like it was actually you who put ...   
159570  fff46fc426af1f9a  "\nAnd ... I really don't think you understand...   

        toxic  
0           0  
1           0  
2           0  
3           0  
4           0  
...       ...  
159566      0  
159567      0  
159568      0  
159569      0  
159570      0  

[159571 rows x 3 columns]

In [9]:
toxic_data = toxic_data.rename(columns={"toxic": "label"})

toxic_data.head(15)

id                                       comment_text  label
0   0000997932d777bf  Explanation\nWhy the edits made under my usern...      0
1   000103f0d9cfb60f  D'aww! He matches this background colour I'm s...      0
2   000113f07ec002fd  Hey man, I'm really not trying to edit war. It...      0
3   0001b41b1c6bb37e  "\nMore\nI can't make any real suggestions on ...      0
4   0001d958c54c6e35  You, sir, are my hero. Any chance you remember...      0
5   00025465d4725e87  "\n\nCongratulations from me as well, use the ...      0
6   0002bcb3da6cb337       COCKSUCKER BEFORE YOU PISS AROUND ON MY WORK      1
7   00031b1e95af7921  Your vandalism to the Matt Shirvington article...      0
8   00037261f536c51d  Sorry if the word 'nonsense' was offensive to ...      0
9   00040093b2687caa  alignment on this subject and which are contra...      0
10  0005300084f90edc  "\nFair use rationale for Image:Wonju.jpg\n\nT...      0
11  00054a5e18b50dd4  bbq \n\nbe a man and lets discuss it-maybe ove...      0
12  0005c987bdfc9d4b  Hey... what is it..\n@ | talk .\nWhat is it......      1
13  0006f16e4e9f292e  Before you start throwing accusations and warn...      0
14  00070ef96486d6f9  Oh, and the girl above started her arguments w...      0

In [11]:
# toxic_data['label'] = toxic_data['label'].astype(float)

In [10]:
import os
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from pathlib import Path

#from sklearn.model_selection import train_test_split
# Hugging Face
from datasets import Dataset, load_dataset
from transformers import AutoModel, AutoTokenizer, utils
utils.logging.set_verbosity_error()  # Suppress standard warnings

from transformers import TrainingArguments, Trainer
from transformers import AutoModelForSequenceClassification, AutoTokenizer


In [11]:
!pip install datasets


# Topic: Classification of emails

Upload the Data_small.zip file into Colab session memory. I first had 4x as many text files in the dataset, but it way too big to train on Colab. It couldn't fit into the 16GB GPU RAM.

It contains a subset from a Kaggle dataset, dealing with emails about a couple of topics.
Dataset from: https://www.kaggle.com/datasets/dipankarsrirag/topic-modelling-on-emails

This subset dataset contains emails that have been given a main topic: crime, politics, or science. When an email belongs to a certain topic, it's stored in that particular folder.

But, there's an issue: the same email can belong to multiple topics, so it's stored in multiple folders... For this example, we want to do a regular multi-class sequence classification, using a pretrained HuggingFace model. Not a multilabel.

So, first we need do a bit of preprocessing, making sure a single email, only belongs to one class. We'll randomly pick a class when we encounter a duplicate.

Credits to Bing Chat (ChatGPT) for providing some coding assistance for the preprocessing code below...

## Step 1: Loading the data & cleaning

### Unzip the data

In [12]:
ds = Dataset.from_pandas(toxic_data[['id','comment_text', 'label']])

# ds = ds.remove_columns('__index_level_0__')

In [13]:
ds

Dataset({
    features: ['id', 'comment_text', 'label'],
    num_rows: 159571
})

### Removing duplicates

In [14]:
id2label = { 0:"Not Toxic",1: "Toxic"}
label2id = {"Not Toxic":0,"Toxic":1}


### Loading data into pandas dataframe

### Encoding the labels

Since the labels are just 3 different strings, we need to use an encoding technique, because in classification, we need the output to be in some sort of number, so we can calculate a loss between the prediction and the true ground label.

We could use the LabelEncoder from sklearn, but HuggingFace provides something similar, the label2id library.

### Loading the dataframe into a HuggingFace dataset

# Step 2: Tokenize your data

To start tokenizing our data, we first must determine our pre-trained model from HuggingFace, we want to use. This is necessary, because each model uses its own style of tokenization, and since we want to apply transfer learning (pre-trained model), we need to same kind of preprocessing to be used on our own dataset.

Luckily, HuggingFace facilitates this rather elegantly, with the use of an AutoTokenizer that will automatically use the correct tokenization and numericalization on our data (linking of ids of a vocab to our tokens, a vocab that is also pretrained).

In [15]:
pretrained_model = 'distilbert-base-cased' #'distilbert-base-uncased' is better, but larger/heavier on GPU
# model above might still give problems with Google Colab max GPU-RAM
# alternative might be:
# pretrained_model = 'microsoft/Multilingual-MiniLM-L12-H384' # but padding is an issue with this one

In [16]:
# use_fast=False if not using CUDA
tokenizer = AutoTokenizer.from_pretrained(pretrained_model, use_fast =True)

tokenizer_config.json:   0%|          | 0.00/29.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/465 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/213k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/436k [00:00<?, ?B/s]

Since we want to apply this to an entire dataset, we create a function, so we can map it to our dataset. We'll use truncation=True to cut of sequences that are too lengthy for our pretrained model, and for those that are to short, we could use the max_length padding.


But, according to HuggingFace docs, it's more efficient to use a DataCollatorWithPadding. It will dynamically pad the sentences to the longest length in a batch during collation (creating a batch for processing, like training). This saves memory and compute (when we have short sentences, which we don't).

We'll use a cut-of lenght of 128, instead of the default max_size of 512. This will conserve memory, but ofcourse we'll only capture the very beginning of the mails.

So, when we apply this preprocessing to our data, all sequences of tokens have the same length. That's important, because we want to batch train, train in parallel. BTW: we kind of did the same thing in our CNNs of 'old'. All images needed to be of the same size...

In [17]:
def preprocess(x):
    return tokenizer(x["comment_text"], truncation=True, max_length=128)

In [18]:
tok_ds = ds.map(preprocess, batched=True)
tok_ds

Map:   0%|          | 0/159571 [00:00<?, ? examples/s]

Dataset({
    features: ['id', 'comment_text', 'label', 'input_ids', 'attention_mask'],
    num_rows: 159571
})

So, let's make a DataCollator that will apply padding to our data when we create a batch. This will be used when we train or test our model with batches of data (see below when we use the Trainer)

In [19]:
from transformers import DataCollatorWithPadding
data_collator = DataCollatorWithPadding(tokenizer=tokenizer, padding='max_length')

# Side-step: investigating our tokenizer

You may have noticed, that applying a tokenizer on our data, the HuggingFace library added 'input_ids', and 'attention_mask'. The input_ids is the numericalization of the tokens (lookup table for the word embeddings our model used). The attention_mask is used for the padding part. If padding was used to create equal length tokens, this mask will let the model know not to pay any attention to these padded items.

In [ ]:
#Let's check a row in our dataset

row = tok_ds[0]
row

{'file_id': '60226',
 'email_text': '\nIn <1pq7rj$q2u@access.digex.net> prb@access.digex.com (Pat) writes:\n\n>In article <1993Apr5.160550.7592@mksol.dseg.ti.com> mccall@mksol.dseg.ti.com (fred j mccall 575-3539) writes:\n>|\n>|I think this would be a great way to build it, but unfortunately\n>|current spending rules don\'t permit it to be workable.  For this to\n>|work it would be necessary for the government to guarantee a certain\n>|minimum amount of business in order to sufficiently reduce the risk\n>|enough to make this attractive to a private firm.  Since they\n>|generally can\'t allocate money except one year at a time, the\n>|government can\'t provide such a tenant guarantee.\n\n\n>Fred.\n\n>\tTry reading a bit.  THe government does lots of multi year\n>contracts with Penalty for cancellation clauses.  They just like to be\n>damn sure they know what they are doing before they sign a multi year\n>contract.   THe reason they aren\'t cutting defense spending as much\n>as they woul

In [ ]:
tokens = tokenizer.tokenize("This is the last day of our supercalifragilisticexpialidocious 'From Machine Learning to Deep Learning'-course! Hope you enjoyed it!")
tokens

['This',
 'is',
 'the',
 'last',
 'day',
 'of',
 'our',
 'super',
 '##cal',
 '##if',
 '##rag',
 '##ilis',
 '##tic',
 '##ex',
 '##pia',
 '##lid',
 '##oc',
 '##ious',
 "'",
 'From',
 'Machine',
 'Learning',
 'to',
 'Deep',
 'Learning',
 "'",
 '-',
 'course',
 '!',
 'Hope',
 'you',
 'enjoyed',
 'it',
 '!']

In [ ]:
ids = tokenizer.convert_tokens_to_ids(tokens)
ids

[1188,
 1110,
 1103,
 1314,
 1285,
 1104,
 1412,
 7688,
 7867,
 8914,
 20484,
 22279,
 2941,
 11708,
 15748,
 17299,
 13335,
 4179,
 112,
 1622,
 7792,
 9681,
 1106,
 7786,
 9681,
 112,
 118,
 1736,
 106,
 5977,
 1128,
 4927,
 1122,
 106]

In [ ]:
decode_string = tokenizer.decode(ids)
decode_string

"This is the last day of our supercalifragilisticexpialidocious'From Machine Learning to Deep Learning'- course! Hope you enjoyed it!"

# Step 3: Create train and test (validation) set

In [21]:
# Split the dataset into train and valid sets (here we use 70/30 split)
dataset = tok_ds.train_test_split(test_size=0.3)

In [22]:
dataset

DatasetDict({
    train: Dataset({
        features: ['id', 'comment_text', 'label', 'input_ids', 'attention_mask'],
        num_rows: 111699
    })
    test: Dataset({
        features: ['id', 'comment_text', 'label', 'input_ids', 'attention_mask'],
        num_rows: 47872
    })
})

In [23]:
tok_train_dataset = dataset["train"]
tok_test_dataset = dataset["test"]

# Step 4: Create an evaluation metric

Since we're doing NLP, there are a lot of different ways to evaluate NLP tasks. Luckily, now, we're only doing classification. So, creating an evaluation function is rather straightforward

In [24]:
import evaluate
accuracy = evaluate.load("accuracy")

In [25]:
# def compute_metrics(eval_pred):
#     predictions, labels = eval_pred
#     predictions = np.argmax(predictions, axis=1)
#     return accuracy.compute(predictions=predictions, references=labels)

def compute_metrics(eval_pred):
    predictions, toxic= eval_pred
    predictions = np.argmax(predictions, axis=1)
    return accuracy.compute(predictions=predictions, references=toxic)


In [ ]:
# Define some metrics to evaluate the model performance
#from sklearn.metrics import accuracy_score, f1_score
#def compute_metrics(pred):
#  labels = pred.label_ids
#  preds = pred.predictions.argmax(-1)
#  f1 = f1_score(labels, preds, average="weighted")
#  acc = accuracy_score(labels, preds)
#  return {"accuracy": acc, "f1": f1}

# Step 5: download a model to apply to our data

In [26]:
from transformers import AutoModelForSequenceClassification

model = AutoModelForSequenceClassification.from_pretrained(pretrained_model, num_labels=2, id2label=id2label, label2id=label2id, output_attentions=True)

# model = CustomModel.from_pretrained(pretrained_model, num_labels=1, id2label=id2label, label2id=label2id, output_attentions=True)


# output_attentions=True: needed for bertviz


model.safetensors:   0%|          | 0.00/263M [00:00<?, ?B/s]

# Sidestep: Visualizing attention mechanism

Without any training/fine-tuning, we can run the pretrained model on a sequence, and watch the attention mechanism in action. We will use our own sentence, so we can observe some patterns emerging.

In [ ]:
inputs = tokenizer.encode("He deposited some money in the bank. Then, he went for a walk on the river bank.", return_tensors='pt')
outputs = model(inputs)
attention = outputs[-1]  # Output includes attention weights when output_attentions=True
tokens = tokenizer.convert_ids_to_tokens(inputs[0])

Let's visualize a single head from our Transformer network, so we can see the attention mechanism work. Notice that we can select which layer. Remember: a Transformer network has several layers (and also several attention heads).

In [ ]:
from bertviz import head_view
# https://github.com/jessevig/bertviz
head_view(attention, tokens)

<IPython.core.display.Javascript object>

Ofcourse, Bert and other models, have multiple heads, and multiple layers. If we want to visualize the entire thing:

In [ ]:
from bertviz import model_view
model_view(attention, tokens)

<IPython.core.display.Javascript object>

# Step 6. Finetune pre-trained model

To create a Trainer, we first need to define our training arguments. BTW setting a good learning rate is pretty tricky in HuggingFace right now. It's more or less trial and error. There's no LRFinder like in Fastai, or a fit_one_cylce kind of scheme.

But, they promise there will be soon...

In [27]:
# Define some training arguments
from transformers import TrainingArguments

training_args = TrainingArguments(
    output_dir="./results",
    learning_rate=2e-5,
    warmup_ratio=0.1,
    lr_scheduler_type="cosine",
    fp16=True,
    # gradient_checkpointing=True, #according to Bing Chat this will do a trade-off between speed and memory usage, but distilbert doesn't support it
    #per_device_train_batch_size=2,#16 is better, but requires more RAM
    #per_device_eval_batch_size=2, #16 is better, but requires more RAM
    num_train_epochs=2,
    weight_decay=0.01,
    #evaluation_strategy="epoch",
    #save_strategy="epoch",
    #load_best_model_at_end=True
)


Now, it's finally time to create our Trainer, and start our finetuning job.

In [28]:
import os
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "max_split_size_mb:128"

In [ ]:
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=tok_train_dataset,
    eval_dataset=tok_test_dataset,
    tokenizer=tokenizer,
    data_collator=data_collator,
    compute_metrics=compute_metrics,
)

trainer.train()



In [ ]:
trainer.save_model("comment_finetuned")

In [36]:
from transformers import AutoModelForSequenceClassification, AutoTokenizer

model_path = "comment_finetuned"
model = AutoModelForSequenceClassification.from_pretrained(model_path)
tokenizer = AutoTokenizer.from_pretrained(model_path)


In [ ]:
# input_text = "i love you "
inputs = tokenizer(input_text, return_tensors="pt")


In [37]:
outputs = model(**inputs)
predictions = outputs.logits.argmax(dim=1)

predicted_label_index = predictions.item()


# Adjust for zero-based indexing
predicted_label_index += 1

# Make sure to check if the adjusted index is within the range of your labels
if predicted_label_index in id2label:
    predicted_label = id2label[predicted_label_index]
    print("Predicted label:", predicted_label)
else:
    print("Invalid label index:", predicted_label_index)




NameError: ignored

In [ ]:
# print("Predicted class:", predictions.item())


Predicted class: 0


# Final Step: Inference time

Due to restrictions on Colab for GPU usage, I couldn't test this step on Colab. But it should work, in theory...

Drag&drop the test_file_Science.txt into session memory of Colab, to run an inference test.

When that's done, we can read it as a pandas dataframe, and put the contents in column 'email_text', just as our training data. That way we can use our previous preprocessing function.

In [68]:
# file= "test_file_Science.txt"

# # Open the txt file and read it as a single string
# with open(file, 'r') as f:
#     text = f.read()
#     row = {"file_id": '1', "email_text": text, "labels": 'Science'}

# # Create a pandas dataframe
# df_test = pd.DataFrame([row])

# first_comment = toxic_data['comment_text'].iloc[0]

first_comment = "you smell like shit please do not come near me idiot"

In [ ]:
# # df_test["email_text"

# df_test = pd.DataFrame[first_comment]

TypeError: ignored

Since we defined our preprocessing function earlier, we can use it here as well, to get the same kind of preprocessing, before giving the data to our model to do inferencing.


Our code that we used:

```
def preprocess(x):
    return tokenizer(x["email_text"], truncation=True, max_length=128)
```

So, we first have to inject our text into a pandas dataframe, under the column 'email-text', and then we can tokenize it!

In [69]:
tok_test = tokenizer(first_comment, truncation=True, max_length=128, return_tensors="pt")

In [70]:
tok_test

{'input_ids': tensor([[  101,  1128,  4773,  1176,  4170,  4268,  1202,  1136,  1435,  1485,
          1143, 10696,   102]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]])}

In [71]:
from transformers import AutoModelForSequenceClassification
import torch

model = AutoModelForSequenceClassification.from_pretrained("comment_finetuned")
with torch.no_grad():
    logits = model(**tok_test).logits


In [72]:
predicted_class_id = logits.argmax().item()
# predicted_class_id += 1

# Make sure to check if the adjusted index is within the range of your labels
if predicted_class_id in model.config.id2label:
    predicted_label = model.config.id2label[predicted_class_id]
    print("Predicted label:", predicted_label)
else:
    print("Invalid label index:", predicted_class_id)


Predicted label: Toxic


In [73]:
import shutil
from google.colab import files

# Replace with your folder path
folder_path = '/content/comment_finetuned'

# Zip the folder
shutil.make_archive('/content/comment_finetuned', 'zip', folder_path)

# Download the zip file
files.download('/content/comment_finetuned.zip')


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Whoops... It didn't do a good job, just yet. I probably need to use a lot more than the first 128 chars of the email to be able to classify it correctly. Or I need to train/finetune the model some more/longer. Or even play with the learning rate, and so on.


But hopefully, you now have a working knowledge of how you can use a HuggingFace model to your own data.